In [1]:
from scgraph_data.world_railways import world_railways_geograph as used_geograph
from bmsspy.bmssp_solver import BmsspCore
import folium
import branca.colormap as bcm

In [2]:
# Indianapolis, IN
origin_id = used_geograph.add_node({'latitude': 39.7684, 'longitude': -86.1581}, circuity=1.0)

bmssp_obj = BmsspCore(used_geograph.graph, origin_id)

arcs = []
for current, predecessor in enumerate(bmssp_obj.predecessor):
    if predecessor == -1:
        continue
    arcs.append((used_geograph.nodes[predecessor], used_geograph.nodes[current]))

In [3]:

# Start the map centered at the first point
start_lat, start_lon = used_geograph.nodes[origin_id]
m = folium.Map(location=[start_lat, start_lon], zoom_start=5)
folium.PolyLine(locations=arcs, color='blue').add_to(m)
# m


In [4]:
predecessors = bmssp_obj.predecessor
distance_matrix = bmssp_obj.distance_matrix

outflows = [[] for _ in range(len(predecessors))]
for out_idx, in_idx in enumerate(predecessors):
    outflows[in_idx].append(out_idx)

tips = [idx for idx in range(len(distance_matrix)) if len(outflows[idx])!=1 and predecessors[idx] !=-1]

In [5]:
new_arcs = []
while tips:
    end_id = tips.pop()
    end_distance = distance_matrix[end_id]
    current_id = end_id
    branch = [end_id]
    while True:
        current_id = predecessors[current_id]
        if current_id == -1:
            break
        branch.append(current_id)
        if len(outflows[current_id]) > 1:
            break
    branch.reverse()
    new_arcs.append({
       'line': [used_geograph.nodes[i] for i in branch],
       'distance_km': end_distance
    })

In [6]:
colormap = bcm.LinearColormap(['green', 'yellow', 'red'], vmin=0, vmax=max([i for i in distance_matrix if i < float('inf')]))
colormap.caption = 'Distance from Indianapolis (km)'

# Step 3: Create map centered on first point
m = folium.Map(location=used_geograph.nodes[origin_id], zoom_start=4)

# Step 4: Add each line with color based on distance
for item in new_arcs:
    color = colormap(item['distance_km'])
    folium.PolyLine(
        locations=item['line'],
        color=color,
        weight=3,
        tooltip=f"KM: {item['distance_km']}"
    ).add_to(m)

# Step 5: Add the color legend
colormap.add_to(m)

m